In [32]:
import numpy as np
from qiskit_nature.second_q.algorithms import GroundStateSolver
from qiskit_nature.second_q.algorithms import GroundStateEigensolver
from qiskit_algorithms import NumPyMinimumEigensolver
from qiskit_nature.second_q.drivers import MethodType, PySCFDriver
from qiskit_nature.second_q.operators import ElectronicIntegrals
from qiskit_nature.second_q.problems import ElectronicBasis, ElectronicStructureResult
from qiskit_nature.second_q.properties import ElectronicDensity
from qiskit_nature.second_q.transformers import ActiveSpaceTransformer, BasisTransformer
from qiskit_nature.second_q.problems import ElectronicBasis, ElectronicStructureProblem
from qiskit_nature.second_q.mappers import ParityMapper

from qiskit_nature.settings import settings
settings.use_symmetry_reduced_integrals = True


In [16]:
# setup driver
omega = 1.0
driver = PySCFDriver(
atom="O 0.0 0.0 0.115; H 0.0 0.754 -0.459; H 0.0 -0.754 -0.459",
# atom=open('PSPCz.xyz').read(),
basis="6-31g*",
method=MethodType.RKS,
xc_functional=f"ldaerf + lr_hf({omega})",
xcf_library="xcfun",
)
# 1. run the reference calculation
driver.run_pyscf()


In [17]:
'''
 2. Build the total Hamiltonian outside of a Problem instance
 Use of QCSchema
'''
from qiskit_nature.second_q.formats.qcschema import QCSchema
from qiskit_nature.second_q.formats import qcschema_translator 
from qiskit_nature.second_q.operators import PolynomialTensor

qcschema = driver.to_qcschema(include_dipole=True)
hamiltonian = qcschema_translator._get_mo_hamiltonian_direct(qcschema)
print(hamiltonian.second_q_op())

hamiltonian.nuclear_repulsion_energy = driver._mol.energy_nuc()

# To included the constant nuclear_repulsion_energy in the second_q_op
e_nuc = hamiltonian.nuclear_repulsion_energy
hamiltonian.electronic_integrals.alpha += PolynomialTensor({"": e_nuc})
# hamiltonian.nuclear_repulsion_energy = None

Fermionic Operator
number spin orbitals=36, number terms=116520
  -33.02337850280139 * ( +_0 -_0 )
+ 0.6864741651861028 * ( +_0 -_1 )
+ 0.24074741430337587 * ( +_0 -_3 )
+ 0.2418910871528054 * ( +_0 -_5 )
+ -0.11536943978223625 * ( +_0 -_9 )
+ -0.2742677269186201 * ( +_0 -_10 )
+ -0.5768235575437899 * ( +_0 -_12 )
+ 0.03432260434843342 * ( +_0 -_13 )
+ -0.10234651326816557 * ( +_0 -_16 )
+ 0.6864741651861069 * ( +_1 -_0 )
+ -7.8078808716121255 * ( +_1 -_1 )
+ -0.23001874400834235 * ( +_1 -_3 )
+ -1.1003814265169514 * ( +_1 -_5 )
+ 0.5158001317553073 * ( +_1 -_9 )
+ 0.4140855580327377 * ( +_1 -_10 )
+ 1.3682406836538898 * ( +_1 -_12 )
+ -0.08354312560194344 * ( +_1 -_13 )
+ 0.12220749658791695 * ( +_1 -_16 )
+ -6.767730983816509 * ( +_2 -_2 )
+ 1.3857994387585575 * ( +_2 -_6 )
+ 0.10747402698265174 * ( +_2 -_7 )
+ 1.587380045059269 * ( +_2 -_11 )
+ 0.21835275569642273 * ( +_2 -_17 )
+ 0.24074741430337762 * ( +_3 -_0 )
+ -0.23001874400834244 * ( +_3 -_1 )
+ -6.9923694044428855 * ( +_3 -_

In [18]:
# 2. build the AO-to-MO basis transformer to ensure constant MOs during entire procedure
(
    mo_coeff,
    mo_coeff_b,
) = driver._expand_mo_object(  
    driver._calc.mo_coeff, array_dimension=3  
)

basis_trafo = BasisTransformer(
            ElectronicBasis.AO,
            ElectronicBasis.MO,
            ElectronicIntegrals.from_raw_integrals(mo_coeff, h1_b=mo_coeff_b),
        )

In [19]:
# Somes variables needed
total_num_particles = driver._mol.nelec
total_num_spatial_orbitals = driver._mol.nao # hamiltonian.register_length
total_num_electrons = driver._mol.nelectron

# Alpha-spin
num_alpha = total_num_particles[0] # qcschema.properties.calcinfo_nalpha
orbital_occupations = np.asarray([1.0] * num_alpha 
                                 + [0.0] * (total_num_spatial_orbitals - num_alpha))
# Beta-spin
num_beta = total_num_particles[1] # , qcschema.properties.calcinfo_nbeta
orbital_occupations_b = np.asarray([1.0] * num_beta 
                                   + [0.0] * (total_num_spatial_orbitals - num_beta))
total_mo_density = ElectronicDensity.from_orbital_occupation(
        orbital_occupations,
        orbital_occupations_b,
        include_rdm2=False,
    )

In [20]:
# Initialize the transformer
transformer =  ActiveSpaceTransformer(2,2)

# Prepare the active space
transformer.prepare_active_space(total_num_particles, total_num_spatial_orbitals,
                                 occupation_alpha=orbital_occupations, 
                                 occupation_beta=orbital_occupations_b,)
# Determine the active space
as_orbitals = transformer._determine_active_space(total_num_electrons, total_num_spatial_orbitals)[0]


In [22]:
# also initialize the history of the active densities
# NOTE: this list tracks the active densities in their reduced dimension: i.e. the active
# dimension
active_density_history = [
    transformer.active_basis.transform_electronic_integrals(
        total_mo_density
    )
]
# also initialize the inactive density in the AO basis (which remains constant at all times)
inactive_ao_density = basis_trafo.invert().transform_electronic_integrals(
    total_mo_density
    - transformer.active_basis.invert().transform_electronic_integrals(
        active_density_history[-1]
    )
)

# 5. prepare some variables which we need to keep track of
e_nuc = driver._mol.energy_nuc()
e_tot = driver._calc.e_tot  # pylint: disable=protected-access
e_next = float("NaN")
e_prev = float("NaN")
converged = False
n_iter = 0
max_iter  = 10
threshold = 1e-2

In [33]:
# 6. finally run the iterative embedding

while n_iter < max_iter:
    n_iter += 1

    # a) expand the active density into the dimensions of the total system
    active_mo_density = (
        transformer.active_basis.invert().transform_electronic_integrals(
            active_density_history[-1]
        )
    )

    # b) transform the active density into the AO basis
    active_ao_density = basis_trafo.invert().transform_electronic_integrals(
        active_mo_density
    )

    # c) compute the total density in the AO basis
    total_ao_density = inactive_ao_density + active_ao_density

    # d) translate the total density into the form required by PySCF
    if basis_trafo.coefficients.beta.is_empty():
        rho = np.asarray(total_ao_density.trace_spin()["+-"])
    else:
        rho = np.asarray(
            [total_ao_density.alpha["+-"], total_ao_density.beta["+-"]]
        )

    # e) evaluate the total energy at the new total density
    e_tot = driver._calc.energy_tot(dm=rho)  # pylint: disable=protected-access
    # f) also evaluate the total Fock operator at the new total density
    (
        fock_a,
        fock_b,
    ) = driver._expand_mo_object(  # pylint: disable=protected-access
        driver._calc.get_fock(dm=rho),  # pylint: disable=protected-access
        array_dimension=3,
    )

    # g) update the active space transformer components
    transformer.active_density = active_mo_density
    transformer.reference_inactive_energy = e_tot - e_nuc
    transformer.reference_inactive_fock = (
        basis_trafo.transform_electronic_integrals(
            ElectronicIntegrals.from_raw_integrals(fock_a, h1_b=fock_b)
        )
    )

    # h) use the updated active space transformer to reduce the problem to the active space
    reduced_hamiltonian = transformer.transform_hamiltonian(hamiltonian)
    problem = ElectronicStructureProblem(reduced_hamiltonian)

    # i) solve the active space problem
    # setup solver
    mapper = ParityMapper(num_particles=(2, 2))
    solver = NumPyMinimumEigensolver()
    solver.filter_criterion = lambda state, val, aux: np.isclose(
        aux["ParticleNumber"][0], 4.0
    )
    algo = GroundStateEigensolver(mapper, solver)

    result = algo.solve(problem)

    # j) append the reduced-size active density in the MO basis to the history, taking into
    # account any user-specified damping procedure
    active_density_history.append(
        damp_active_density(
            active_density_history + [result.electronic_density]
        )
    )

    # k) check for convergence
    e_prev = e_next
    e_next = result.total_energies[0]
    converged = np.abs(e_prev - e_next) < threshold
    if converged:
        break


TypeError: 'NoneType' object is not subscriptable

In [ ]:
# h) use the updated active space transformer to reduce the problem to the active space
    as_problem = transformer.transform(problem)

    # i) solve the active space problem
    result = solver.solve(as_problem)

    # j) append the reduced-size active density in the MO basis to the history, taking into
    # account any user-specified damping procedure
    active_density_history.append(
        damp_active_density(
            active_density_history + [result.electronic_density]
        )
    )

    # k) check for convergence
    e_prev = e_next
    e_next = result.total_energies[0]
    converged = np.abs(e_prev - e_next) < threshold
    if converged:
        break


In [7]:
# 3. generate the problem with range-separated 2-body terms
with driver._mol.with_range_coulomb(  # pylint: disable=protected-access
    omega=omega
):
    problem = driver.to_problem(basis=ElectronicBasis.MO, include_dipole=False)


MemoryError: Unable to allocate 32.0 GiB for an array with shape (4293447445,) and data type float64